In [1]:
%pip install mtcnn pillow matplotlib tensorflow tqdm

Note: you may need to restart the kernel to use updated packages.


In [2]:
%pip install mediapipe

   ---------------------------------------- 0.0/50.8 MB ? eta -:--:--
   ---------------------------------------- 0.3/50.8 MB 8.6 MB/s eta 0:00:06
   ---------------------------------------- 0.4/50.8 MB 12.8 MB/s eta 0:00:04
    --------------------------------------- 1.0/50.8 MB 8.8 MB/s eta 0:00:06
   - -------------------------------------- 1.4/50.8 MB 8.7 MB/s eta 0:00:06
   - -------------------------------------- 1.6/50.8 MB 7.7 MB/s eta 0:00:07
   - -------------------------------------- 2.2/50.8 MB 8.6 MB/s eta 0:00:06
   - -------------------------------------- 2.5/50.8 MB 8.9 MB/s eta 0:00:06
   -- ------------------------------------- 3.2/50.8 MB 9.7 MB/s eta 0:00:05
   --- ------------------------------------ 3.8/50.8 MB 9.8 MB/s eta 0:00:05
   --- ------------------------------------ 4.2/50.8 MB 9.5 MB/s eta 0:00:05
   --- ------------------------------------ 5.0/50.8 MB 10.2 MB/s eta 0:00:05
   ---- ----------------------------------- 5.7/50.8 MB 10.7 MB/s eta 0:00:05
   

In [9]:
%pip install opencv-python pillow numpy

Note: you may need to restart the kernel to use updated packages.


In [5]:
import os
from PIL import Image
from numpy import asarray
from mtcnn.mtcnn import MTCNN
import matplotlib.pyplot as plt
from tqdm import tqdm
from mtcnn import MTCNN

In [ ]:
%pip install retina-face tf-keras

In [2]:
from retinaface import RetinaFace
from PIL import Image
import numpy as np

# Function to extract faces using RetinaFace
def extract_face_3(filename, required_size=(224, 224)):
    # Load image from file
    image = Image.open(filename)
    image = image.convert('RGB')
    pixels = np.asarray(image)
    
    # Detect faces in the image using RetinaFace
    faces = RetinaFace.detect_faces(pixels)
    face_images = []

    # Extract each face
    for key, face in faces.items():
        facial_area = face['facial_area']
        x1, y1, x2, y2 = facial_area
        
        # Correct negative coordinates
        x1, y1, x2, y2 = max(0, x1), max(0, y1), max(0, x2), max(0, y2)
        
        # Extract the face
        face = pixels[y1:y2, x1:x2]
        
        # Resize pixels to the required size
        face_image = Image.fromarray(face)
        face_image = face_image.resize(required_size)
        face_array = np.asarray(face_image)
        face_images.append(face_array)
        
    return face_images

# Example usage
faces = extract_face_3('image00001.jpeg')
for i, face in enumerate(faces):
    Image.fromarray(face).save(f'face_{i+16}.jpg')

24-05-07 08:37:51 - Directory C:\Users\adoye/.deepface created
24-05-07 08:37:51 - Directory C:\Users\adoye/.deepface/weights created
24-05-07 08:37:51 - retinaface.h5 will be downloaded from the url https://github.com/serengil/deepface_models/releases/download/v1.0/retinaface.h5


Downloading...
From: https://github.com/serengil/deepface_models/releases/download/v1.0/retinaface.h5
To: C:\Users\adoye\.deepface\weights\retinaface.h5
100%|██████████| 119M/119M [00:12<00:00, 9.19MB/s] 


In [6]:
# Create the detector, using default weights
detector = MTCNN()

def extract_face(filename, required_size=(224, 224)):
    # Load image from file
    image = Image.open(filename)
    image = image.convert('RGB')
    pixels = asarray(image)
    
    # Detect faces in the image
    results = detector.detect_faces(pixels)
    face_images = []
    
    # Extract each face
    for result in results:
        x1, y1, width, height = result['box']
        x2, y2 = x1 + width, y1 + height
        
        # Correct negative coordinates
        x1, y1, x2, y2 = max(0, x1), max(0, y1), max(0, x2), max(0, y2)
        
        # Extract the face
        face = pixels[y1:y2, x1:x2]
        
        # Resize pixels to the model size
        image = Image.fromarray(face)
        image = image.resize(required_size)
        face_array = asarray(image)
        face_images.append(face_array)
        
    return face_images

In [4]:
import cv2
import mediapipe as mp
from PIL import Image
import numpy as np

# Initialize MediaPipe Face Detection
mp_face_detection = mp.solutions.face_detection
mp_drawing = mp.solutions.drawing_utils

def extract_face_2(filename, required_size=(224, 224)):
    # Load image from file using OpenCV
    image = cv2.imread(filename)
    image_rgb = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)

    # Initialize face detector
    with mp_face_detection.FaceDetection(model_selection=1, min_detection_confidence=0.5) as face_detection:
        results = face_detection.process(image_rgb)

        face_images = []

        if results.detections:
            for detection in results.detections:
                # Extract bounding box coordinates
                bboxC = detection.location_data.relative_bounding_box
                ih, iw, _ = image.shape
                x1, y1 = int(bboxC.xmin * iw), int(bboxC.ymin * ih)
                width, height = int(bboxC.width * iw), int(bboxC.height * ih)
                x2, y2 = x1 + width, y1 + height

                # Correct negative coordinates
                x1, y1, x2, y2 = max(0, x1), max(0, y1), max(0, x2), max(0, y2)

                # Extract the face
                face = image_rgb[y1:y2, x1:x2]

                # Resize pixels to the model size
                image_pil = Image.fromarray(face)
                image_pil = image_pil.resize(required_size)
                face_array = np.asarray(image_pil)
                face_images.append(face_array)

    return face_images

# Example usage
faces = extract_face_2('image00001.jpeg')
for i, face in enumerate(faces):
    Image.fromarray(face).save(f'face_{i+18}.jpg')


In [ ]:

# Directory containing images
directory = 'Orignal Datasets\Auguste_Original'

# Process all images in the directory
for filename in tqdm(os.listdir(directory)):
    path = os.path.join(directory, filename)
    if os.path.isfile(path):
        try:
            faces = extract_face(path)
            for i, face in enumerate(faces):
                # Optionally save each face as an image
                Image.fromarray(face).save(f"TEST\extracted_face_{filename}_{i}.png")
        except Exception as e:
            print(f"Error processing file {filename}: {e}")


In [4]:
# Directory containing images
directory = r'Orignal Datasets\NOT Auguste_Original'

# Process all images in the directory
for filename in tqdm(os.listdir(directory)):
    path = os.path.join(directory, filename)
    if os.path.isfile(path):
        try:
            faces = extract_face(path)
            for i, face in enumerate(faces):
                # Optionally save each face as an image
                Image.fromarray(face).save(rf"Transformed_Datasets\NOT_Auguste_Cropped_224\extracted_face_{filename}_{i}.png")
        except Exception as e:
            print(f"Error processing file {filename}: {e}")


  0%|          | 0/2843 [00:00<?, ?it/s]

1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 642ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 441ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 141ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 108ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 86ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 69ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 46ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 62ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 43ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
97/97 ━━━━━━━━━━━━━━━━━━━━ 1s 8ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 330ms/step


  0%|          | 1/2843 [00:06<5:13:21,  6.62s/it]

1/1 ━━━━━━━━━━━━━━━━━━━━ 219s 219s/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 822ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 430ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 260ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 140ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 115ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 77ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 71ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 59ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 62ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 58ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 54ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 56ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 54ms/step
239/239 ━━━━━━━━━━━━━━━━━━━━ 2s 10ms/step
4/4 ━━━━━━━━━━━━━━━━━━━━ 0s 22ms/step


  0%|          | 2/2843 [04:02<111:27:53, 141.24s/it]

...

100%|█████████▉| 2841/2843 [3:15:25<00:04,  2.46s/it]

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 205ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 170ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 80ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 54ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 52ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 24ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 28ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 23ms/step
8/8 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step 
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step


100%|█████████▉| 2842/2843 [3:15:28<00:02,  2.39s/it]

1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 755ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 408ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 212ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 113ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 74ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 61ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 42ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 35ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 26ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 24ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 26ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step
29/29 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step


100%|██████████| 2843/2843 [3:15:33<00:00,  4.13s/it]
